In [1]:
!pip install accelerate peft bitsandbytes transformers trl

     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 297.4/297.4 kB 9.3 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 199.1/199.1 kB 15.7 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 119.8/119.8 MB 13.9 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 244.1/244.1 kB 26.2 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 510.5/510.5 kB 45.1 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 102.0/102.0 kB 14.3 MB/s eta 0:00:00
  Using cached nvidia_cuda_nvrtc_cu12-12.1.105-py3-none-manylinux1_x86_64.whl (23.7 MB)
  Using cached nvidia_cuda_runtime_cu12-12.1.105-py3-none-manylinux1_x86_64.whl (823 kB)
  Using cached nvidia_cuda_cupti_cu12-12.1.105-py3-none-manylinux1_x86_64.whl (14.1 MB)
  Using cached nvidia_cudnn_cu12-8.9.2.26-py3-none-manylinux1_x86_64.whl (731.7 MB)
  Using cached nvidia_cublas_cu12-12.1.3.1-py3-none-manylinux1_x86_64.whl (410.6 MB)
  Using cached nvidia_cufft_cu12-11.0.2.54-py3-none-manylinux1_x86_64

In [2]:
#In general, there are two foundational models that Mistral released: Mistral 7B v0.1 and Mistral 7B Instruct v0.1. The Mistral 7B v0.1 is the base foundation model, and the Mistral 7B Instruct v0.1 is a Mistral 7B v0.1 model that has been fine-tuned for conversation and question answering.

#We would need a CSV file containing a text column for the fine-tuning with Hugging Face AutoTrain. However, we would use a different text format for the base and instruction models during the fine-tuning.
from datasets import load_dataset
import pandas as pd

# Load the dataset
train =load_dataset("codeparrot/xlcost-text-to-code", "Python-program-level", split='train[:50%]')
#train= load_dataset("codeparrot/xlcost-text-to-code","Python-program-level", split='train[:10%]')
train = pd.DataFrame(train)
train

/usr/local/lib/python3.10/dist-packages/huggingface_hub/utils/_token.py:88: UserWarning: 
The secret `HF_TOKEN` does not exist in your Colab secrets.
To authenticate with the Hugging Face Hub, create a token in your settings tab (https://huggingface.co/settings/tokens), set it as secret in your Google Colab and restart your session.
You will be able to reuse this secret in all of your notebooks.
Please note that authentication is recommended but still optional to access public models or datasets.
  warnings.warn(


Generating train split:   0%|          | 0/9263 [00:00<?, ? examples/s]

Generating test split:   0%|          | 0/887 [00:00<?, ? examples/s]

Generating validation split:   0%|          | 0/472 [00:00<?, ? examples/s]

text  \
0     Maximum Prefix Sum possible by merging two giv...   
1     Check if a number can be represented as sum of...   
2     Generate an N | Python3 program for the above ...   
3     Nth natural number after removing all numbers ...   
4     Check if an integer is rotation of another giv...   
...                                                 ...   
4627  Print all triplets with given sum | Python3 pr...   
4628  Maximum product quadruple ( sub | Python3 prog...   
4629  Maximum product quadruple ( sub | Function to ...   
4630  Minimum value of " max ▁ + ▁ min " in a subarr...   
4631  Stella Octangula Number | Returns value of n *...   

                                                   code  
0     def maxPresum ( a , b ) : NEW_LINE INDENT X = ...  
1     import math NEW_LINE def sumOfTwoCubes ( n ) :...  
2     sieve = [ 1 ] * ( 1000000 + 1 ) NEW_LINE def s...  
3     def findNthNumber ( N ) : NEW_LINE INDENT resu...  
4     import math NEW_LINE def check ( A , B ) : NEW...  
...                                                 ...  
4627  import math as mt NEW_LINE def findTriplets ( ...  
4628  import sys NEW_LINE def maxProduct ( arr , n )...  
4629  def maxProduct ( arr , n ) : NEW_LINE INDENT i...  
4630  def maxSum ( arr , n ) : NEW_LINE INDENT if ( ...  
4631  def f ( n ) : NEW_LINE INDENT return n * ( 2 *...  

[4632 rows x 2 columns]

In [3]:
train.rename(columns={'text': 'instruction', 'code': 'output'}, inplace=True)
train

instruction  \
0     Maximum Prefix Sum possible by merging two giv...   
1     Check if a number can be represented as sum of...   
2     Generate an N | Python3 program for the above ...   
3     Nth natural number after removing all numbers ...   
4     Check if an integer is rotation of another giv...   
...                                                 ...   
4627  Print all triplets with given sum | Python3 pr...   
4628  Maximum product quadruple ( sub | Python3 prog...   
4629  Maximum product quadruple ( sub | Function to ...   
4630  Minimum value of " max ▁ + ▁ min " in a subarr...   
4631  Stella Octangula Number | Returns value of n *...   

                                                 output  
0     def maxPresum ( a , b ) : NEW_LINE INDENT X = ...  
1     import math NEW_LINE def sumOfTwoCubes ( n ) :...  
2     sieve = [ 1 ] * ( 1000000 + 1 ) NEW_LINE def s...  
3     def findNthNumber ( N ) : NEW_LINE INDENT resu...  
4     import math NEW_LINE def check ( A , B ) : NEW...  
...                                                 ...  
4627  import math as mt NEW_LINE def findTriplets ( ...  
4628  import sys NEW_LINE def maxProduct ( arr , n )...  
4629  def maxProduct ( arr , n ) : NEW_LINE INDENT i...  
4630  def maxSum ( arr , n ) : NEW_LINE INDENT if ( ...  
4631  def f ( n ) : NEW_LINE INDENT return n * ( 2 *...  

[4632 rows x 2 columns]

In [4]:
train['instruction'][0], train['output'][0]

('Maximum Prefix Sum possible by merging two given arrays | Python3 implementation of the above approach ; Stores the maximum prefix sum of the array A [ ] ; Traverse the array A [ ] ; Stores the maximum prefix sum of the array B [ ] ; Traverse the array B [ ] ; Driver code',
 'def maxPresum ( a , b ) : NEW_LINE INDENT X = max ( a [ 0 ] , 0 ) NEW_LINE for i in range ( 1 , len ( a ) ) : NEW_LINE INDENT a [ i ] += a [ i - 1 ] NEW_LINE X = max ( X , a [ i ] ) NEW_LINE DEDENT Y = max ( b [ 0 ] , 0 ) NEW_LINE for i in range ( 1 , len ( b ) ) : NEW_LINE INDENT b [ i ] += b [ i - 1 ] NEW_LINE Y = max ( Y , b [ i ] ) NEW_LINE DEDENT return X + Y NEW_LINE DEDENT A = [ 2 , - 1 , 4 , - 5 ] NEW_LINE B = [ 4 , - 3 , 12 , 4 , - 3 ] NEW_LINE print ( maxPresum ( A , B ) ) NEW_LINE')

In [5]:
train

instruction  \
0     Maximum Prefix Sum possible by merging two giv...   
1     Check if a number can be represented as sum of...   
2     Generate an N | Python3 program for the above ...   
3     Nth natural number after removing all numbers ...   
4     Check if an integer is rotation of another giv...   
...                                                 ...   
4627  Print all triplets with given sum | Python3 pr...   
4628  Maximum product quadruple ( sub | Python3 prog...   
4629  Maximum product quadruple ( sub | Function to ...   
4630  Minimum value of " max ▁ + ▁ min " in a subarr...   
4631  Stella Octangula Number | Returns value of n *...   

                                                 output  
0     def maxPresum ( a , b ) : NEW_LINE INDENT X = ...  
1     import math NEW_LINE def sumOfTwoCubes ( n ) :...  
2     sieve = [ 1 ] * ( 1000000 + 1 ) NEW_LINE def s...  
3     def findNthNumber ( N ) : NEW_LINE INDENT resu...  
4     import math NEW_LINE def check ( A , B ) : NEW...  
...                                                 ...  
4627  import math as mt NEW_LINE def findTriplets ( ...  
4628  import sys NEW_LINE def maxProduct ( arr , n )...  
4629  def maxProduct ( arr , n ) : NEW_LINE INDENT i...  
4630  def maxSum ( arr , n ) : NEW_LINE INDENT if ( ...  
4631  def f ( n ) : NEW_LINE INDENT return n * ( 2 *...  

[4632 rows x 2 columns]

In [6]:
train['instruction'].isnull().sum()
print(train[train['instruction'] == ''])

print(train[train['instruction'] == ''].reset_index(drop = True))

Empty DataFrame
Columns: [instruction, output]
Index: []
Empty DataFrame
Columns: [instruction, output]
Index: []


In [7]:
train_chat = train.copy()
print("1111111111111", train_chat)

1111111111111                                             instruction  \
0     Maximum Prefix Sum possible by merging two giv...   
1     Check if a number can be represented as sum of...   
2     Generate an N | Python3 program for the above ...   
3     Nth natural number after removing all numbers ...   
4     Check if an integer is rotation of another giv...   
...                                                 ...   
4627  Print all triplets with given sum | Python3 pr...   
4628  Maximum product quadruple ( sub | Python3 prog...   
4629  Maximum product quadruple ( sub | Function to ...   
4630  Minimum value of " max ▁ + ▁ min " in a subarr...   
4631  Stella Octangula Number | Returns value of n *...   

                                                 output  
0     def maxPresum ( a , b ) : NEW_LINE INDENT X = ...  
1     import math NEW_LINE def sumOfTwoCubes ( n ) :...  
2     sieve = [ 1 ] * ( 1000000 + 1 ) NEW_LINE def s...  
3     def findNthNumber ( N ) : NEW_LINE INDE

In [8]:
##If you want to fine-tune the Mistral 7B Instruct v0.1 for conversation and question answering, we need to follow the chat template format provided by Mistral, shown in the code block below.

#<s>[INST] Instruction [/INST] Model answer</s>[INST] Follow-up instruction [/INST]


#If we use our previous example dataset, we need to reformat the text column. We would use only the data without any input for the chat model.

#Then, we could reformat the data with the following code.

def chat_formatting(data):

  text = f"<s>[INST] {data['instruction']} [/INST] {data['output']} </s>"

  return text

train_chat['text'] = train_chat.apply(chat_formatting, axis =1)
train_chat.to_csv('train_text-to-code.csv', index =False)
print("22222222222", train_chat)

22222222222                                             instruction  \
0     Maximum Prefix Sum possible by merging two giv...   
1     Check if a number can be represented as sum of...   
2     Generate an N | Python3 program for the above ...   
3     Nth natural number after removing all numbers ...   
4     Check if an integer is rotation of another giv...   
...                                                 ...   
4627  Print all triplets with given sum | Python3 pr...   
4628  Maximum product quadruple ( sub | Python3 prog...   
4629  Maximum product quadruple ( sub | Function to ...   
4630  Minimum value of " max ▁ + ▁ min " in a subarr...   
4631  Stella Octangula Number | Returns value of n *...   

                                                 output  \
0     def maxPresum ( a , b ) : NEW_LINE INDENT X = ...   
1     import math NEW_LINE def sumOfTwoCubes ( n ) :...   
2     sieve = [ 1 ] * ( 1000000 + 1 ) NEW_LINE def s...   
3     def findNthNumber ( N ) : NEW_LINE IN

In [9]:
train_chat['text'][0], train_chat

('<s>[INST] Maximum Prefix Sum possible by merging two given arrays | Python3 implementation of the above approach ; Stores the maximum prefix sum of the array A [ ] ; Traverse the array A [ ] ; Stores the maximum prefix sum of the array B [ ] ; Traverse the array B [ ] ; Driver code [/INST] def maxPresum ( a , b ) : NEW_LINE INDENT X = max ( a [ 0 ] , 0 ) NEW_LINE for i in range ( 1 , len ( a ) ) : NEW_LINE INDENT a [ i ] += a [ i - 1 ] NEW_LINE X = max ( X , a [ i ] ) NEW_LINE DEDENT Y = max ( b [ 0 ] , 0 ) NEW_LINE for i in range ( 1 , len ( b ) ) : NEW_LINE INDENT b [ i ] += b [ i - 1 ] NEW_LINE Y = max ( Y , b [ i ] ) NEW_LINE DEDENT return X + Y NEW_LINE DEDENT A = [ 2 , - 1 , 4 , - 5 ] NEW_LINE B = [ 4 , - 3 , 12 , 4 , - 3 ] NEW_LINE print ( maxPresum ( A , B ) ) NEW_LINE </s>',
                                             instruction  \
 0     Maximum Prefix Sum possible by merging two giv...   
 1     Check if a number can be represented as sum of...   
 2     Generate an N | 

In [11]:
train_text_to_code =train_chat.copy()
train_text_to_code.to_csv('data/train_text-to-code.csv', index =False)
print("33333333", train_text_to_code)

33333333                                             instruction  \
0     Maximum Prefix Sum possible by merging two giv...   
1     Check if a number can be represented as sum of...   
2     Generate an N | Python3 program for the above ...   
3     Nth natural number after removing all numbers ...   
4     Check if an integer is rotation of another giv...   
...                                                 ...   
4627  Print all triplets with given sum | Python3 pr...   
4628  Maximum product quadruple ( sub | Python3 prog...   
4629  Maximum product quadruple ( sub | Function to ...   
4630  Minimum value of " max ▁ + ▁ min " in a subarr...   
4631  Stella Octangula Number | Returns value of n *...   

                                                 output  \
0     def maxPresum ( a , b ) : NEW_LINE INDENT X = ...   
1     import math NEW_LINE def sumOfTwoCubes ( n ) :...   
2     sieve = [ 1 ] * ( 1000000 + 1 ) NEW_LINE def s...   
3     def findNthNumber ( N ) : NEW_LINE INDEN

In [12]:
print(train_text_to_code['text'][0])
print(len(train_text_to_code['text'][0]))

<s>[INST] Maximum Prefix Sum possible by merging two given arrays | Python3 implementation of the above approach ; Stores the maximum prefix sum of the array A [ ] ; Traverse the array A [ ] ; Stores the maximum prefix sum of the array B [ ] ; Traverse the array B [ ] ; Driver code [/INST] def maxPresum ( a , b ) : NEW_LINE INDENT X = max ( a [ 0 ] , 0 ) NEW_LINE for i in range ( 1 , len ( a ) ) : NEW_LINE INDENT a [ i ] += a [ i - 1 ] NEW_LINE X = max ( X , a [ i ] ) NEW_LINE DEDENT Y = max ( b [ 0 ] , 0 ) NEW_LINE for i in range ( 1 , len ( b ) ) : NEW_LINE INDENT b [ i ] += b [ i - 1 ] NEW_LINE Y = max ( Y , b [ i ] ) NEW_LINE DEDENT return X + Y NEW_LINE DEDENT A = [ 2 , - 1 , 4 , - 5 ] NEW_LINE B = [ 4 , - 3 , 12 , 4 , - 3 ] NEW_LINE print ( maxPresum ( A , B ) ) NEW_LINE </s>
792


In [2]:
!rm -rf /content/results

In [3]:
#After that, we will load the necessary modules from these libraries.
import os
import torch
from datasets import load_dataset
from transformers import (
    AutoModelForCausalLM,
    AutoTokenizer,
    BitsAndBytesConfig,
    TrainingArguments,
    pipeline,
    logging,
)
from peft import LoraConfig
from trl import SFTTrainer

In [4]:
# Model from Hugging Face hub
base_model = "NousResearch/Llama-2-7b-chat-hf"

# New instruction dataset
guanaco_dataset = "mlabonne/guanaco-llama2-1k"

# Fine-tuned model
new_model = "llama-2-7b-chat-text-to-python"

In [ ]:
#load dataset
'''
import pandas as pd
train_text_to_code =pd.read_csv("/content/data/train_text-to-code.csv")
print("111111111", train_text_to_code.head())
train_text_to_code =train_text_to_code[['text']]
dataset =train_text_to_code.copy()
dataset.head()
'''


In [5]:
import pandas as pd
from sklearn.model_selection import train_test_split
from datasets import Dataset, DatasetDict

# Load the CSV file
df = pd.read_csv("/content/data/train_text-to-code.csv")
#df = df.iloc[0:1500, :]
train_df, val_df = train_test_split(df, test_size=0.2, random_state=42)

# Reset index to remove __index_level_0__
train_df.reset_index(drop=True, inplace=True)
val_df.reset_index(drop=True, inplace=True)

# Create train and validation datasets
train_data = Dataset.from_pandas(train_df[['text']])
eval_data = Dataset.from_pandas(val_df[['text']])

# Create DatasetDict
dataset_dict = DatasetDict({
    "train": train_data,
    "validation": eval_data
})

print(dataset_dict)


DatasetDict({
    train: Dataset({
        features: ['text'],
        num_rows: 3705
    })
    validation: Dataset({
        features: ['text'],
        num_rows: 927
    })
})


In [6]:
dataset_dict['train']['text'], dataset_dict['validation']['text']

(['<s>[INST] Fibbinary Numbers ( No consecutive 1 s in binary ) | function to check if binary representation of an integer has consecutive 1 s ; stores the previous last bit initially as 0 ; if current last bit and previous last bit is 1 ; stores the last bit ; right shift the number ; Driver code [/INST] def checkFibinnary ( n ) : NEW_LINE INDENT prev_last = 0 NEW_LINE while ( n ) : NEW_LINE INDENT if ( ( n & 1 ) and prev_last ) : NEW_LINE INDENT return False NEW_LINE DEDENT prev_last = n & 1 NEW_LINE n >>= 1 NEW_LINE DEDENT return True NEW_LINE DEDENT n = 10 NEW_LINE if ( checkFibinnary ( n ) ) : NEW_LINE INDENT print ( " YES " ) NEW_LINE DEDENT else : NEW_LINE INDENT print ( " NO " ) NEW_LINE DEDENT </s>',
  '<s>[INST] Count numbers less than N containing digits from the given set : Digit DP | Python3 implementation to find the count of numbers possible less than N , such that every digit is from the given set of digits ; Function to convert integer into the string ; Recursive funct

In [7]:
dataset_train = dataset_dict['train']
dataset_val = dataset_dict['validation']

dataset_train

Dataset({
    features: ['text'],
    num_rows: 3705
})

In [8]:
dataset_train['text']

['<s>[INST] Fibbinary Numbers ( No consecutive 1 s in binary ) | function to check if binary representation of an integer has consecutive 1 s ; stores the previous last bit initially as 0 ; if current last bit and previous last bit is 1 ; stores the last bit ; right shift the number ; Driver code [/INST] def checkFibinnary ( n ) : NEW_LINE INDENT prev_last = 0 NEW_LINE while ( n ) : NEW_LINE INDENT if ( ( n & 1 ) and prev_last ) : NEW_LINE INDENT return False NEW_LINE DEDENT prev_last = n & 1 NEW_LINE n >>= 1 NEW_LINE DEDENT return True NEW_LINE DEDENT n = 10 NEW_LINE if ( checkFibinnary ( n ) ) : NEW_LINE INDENT print ( " YES " ) NEW_LINE DEDENT else : NEW_LINE INDENT print ( " NO " ) NEW_LINE DEDENT </s>',
 '<s>[INST] Count numbers less than N containing digits from the given set : Digit DP | Python3 implementation to find the count of numbers possible less than N , such that every digit is from the given set of digits ; Function to convert integer into the string ; Recursive functio

In [9]:
#In our case, we create 4-bit quantization with NF4 type configuration using BitsAndBytes.

compute_dtype = getattr(torch, "float16")

quant_config = BitsAndBytesConfig(
    load_in_4bit=True,
    bnb_4bit_quant_type="nf4",
    bnb_4bit_compute_dtype=compute_dtype,
    bnb_4bit_use_double_quant=False,
)

In [10]:
#We will now load a model using 4-bit precision with the compute dtype "float16" from Hugging Face for faster training.
model = AutoModelForCausalLM.from_pretrained(
    base_model,
    quantization_config=quant_config,
    device_map={"": 0}
)
model.config.use_cache = False
model.config.pretraining_tp = 1

/usr/local/lib/python3.10/dist-packages/huggingface_hub/utils/_token.py:88: UserWarning: 
The secret `HF_TOKEN` does not exist in your Colab secrets.
To authenticate with the Hugging Face Hub, create a token in your settings tab (https://huggingface.co/settings/tokens), set it as secret in your Google Colab and restart your session.
You will be able to reuse this secret in all of your notebooks.
Please note that authentication is recommended but still optional to access public models or datasets.
  warnings.warn(


Loading checkpoint shards:   0%|          | 0/2 [00:00<?, ?it/s]

/usr/local/lib/python3.10/dist-packages/transformers/generation/configuration_utils.py:410: UserWarning: `do_sample` is set to `False`. However, `temperature` is set to `0.9` -- this flag is only used in sample-based generation modes. You should set `do_sample=True` or unset `temperature`. This was detected when initializing the generation config instance, which means the corresponding file may hold incorrect parameterization and should be fixed.
  warnings.warn(
/usr/local/lib/python3.10/dist-packages/transformers/generation/configuration_utils.py:415: UserWarning: `do_sample` is set to `False`. However, `top_p` is set to `0.6` -- this flag is only used in sample-based generation modes. You should set `do_sample=True` or unset `top_p`. This was detected when initializing the generation config instance, which means the corresponding file may hold incorrect parameterization and should be fixed.
  warnings.warn(
/usr/local/lib/python3.10/dist-packages/transformers/generation/configuratio

In [11]:
#Next, we will load the tokenizer from Hugginface and set padding_side to “right” to fix the issue with fp16.
tokenizer = AutoTokenizer.from_pretrained(base_model, trust_remote_code=True)
tokenizer.pad_token = tokenizer.eos_token
tokenizer.padding_side = "right"

In [12]:
#Traditional fine-tuning of pre-trained language models (PLMs) requires updating all of the model's parameters, which is computationally expensive and requires massive amounts of data.

#Parameter-Efficient Fine-Tuning (PEFT) works by only updating a small subset of the model's most influential parameters, making it much more efficient.
peft_params = LoraConfig(
    lora_alpha=16,
    lora_dropout=0.1,
    r=64,
    bias="none",
    task_type="CAUSAL_LM",
)

In [15]:
#hyperparameters that can be used to optimize the training process:
training_params = TrainingArguments(
    output_dir="./results",
    num_train_epochs=1,
    per_device_train_batch_size=1,
    gradient_accumulation_steps=8,
    optim="paged_adamw_32bit",
    save_steps=25,
    logging_steps=25,
    learning_rate=2e-4,
    weight_decay=0.001,
    fp16= True,
    bf16=False,
    max_grad_norm=0.3,
    max_steps=-1,
    warmup_ratio=0.03,
    group_by_length=True,
    lr_scheduler_type="constant",
    report_to="tensorboard",
    evaluation_strategy="epoch"
)

In [16]:
#Supervised fine-tuning (SFT) is a key step in reinforcement learning from human feedback (RLHF). The TRL library from HuggingFace provides an easy-to-use API to create SFT models and train them on your dataset with just a few lines of code. It comes with tools to train language models using reinforcement learning, starting with supervised fine-tuning, then reward modeling, and finally, proximal policy optimization (PPO).

#We will provide SFT Trainer the model, dataset, Lora configuration, tokenizer, and training parameters.

trainer = SFTTrainer(
    model=model,
    train_dataset=dataset_train,
    eval_dataset=dataset_val,
    peft_config=peft_params,
    dataset_text_field="text",
    max_seq_length=None,
    tokenizer=tokenizer,
    args=training_params,
    packing=False,
)

/usr/local/lib/python3.10/dist-packages/trl/trainer/sft_trainer.py:246: UserWarning: You didn't pass a `max_seq_length` argument to the SFTTrainer, this will default to 1024
  warnings.warn(


Map:   0%|          | 0/3705 [00:00<?, ? examples/s]

Map:   0%|          | 0/927 [00:00<?, ? examples/s]

/usr/local/lib/python3.10/dist-packages/accelerate/accelerator.py:436: FutureWarning: Passing the following arguments to `Accelerator` is deprecated and will be removed in version 1.0 of Accelerate: dict_keys(['dispatch_batches', 'split_batches', 'even_batches', 'use_seedable_sampler']). Please pass an `accelerate.DataLoaderConfiguration` instead: 
dataloader_config = DataLoaderConfiguration(dispatch_batches=None, split_batches=False, even_batches=True, use_seedable_sampler=True)
  warnings.warn(


In [17]:
# Train model
trainer.train()

TrainOutput(global_step=463, training_loss=0.8469729310235503, metrics={'train_runtime': 1944.7296, 'train_samples_per_second': 1.905, 'train_steps_per_second': 0.238, 'total_flos': 6.448864527325594e+16, 'train_loss': 0.8469729310235503, 'epoch': 1.0})

In [28]:
# Save trained model
trainer.model.save_pretrained(new_model)
trainer.tokenizer.save_pretrained(new_model)


('llama-2-7b-chat-text-to-python/tokenizer_config.json',
 'llama-2-7b-chat-text-to-python/special_tokens_map.json',
 'llama-2-7b-chat-text-to-python/tokenizer.model',
 'llama-2-7b-chat-text-to-python/added_tokens.json',
 'llama-2-7b-chat-text-to-python/tokenizer.json')

In [22]:
#automatically push to hub with all require things
trainer.push_to_hub("end of training")

training_args.bin:   0%|          | 0.00/4.86k [00:00<?, ?B/s]

events.out.tfevents.1713195069.710a066a8bde.9642.0:   0%|          | 0.00/9.46k [00:00<?, ?B/s]

Upload 4 LFS files:   0%|          | 0/4 [00:00<?, ?it/s]

adapter_model.safetensors:   0%|          | 0.00/134M [00:00<?, ?B/s]

tokenizer.model:   0%|          | 0.00/500k [00:00<?, ?B/s]

CommitInfo(commit_url='https://huggingface.co/kr-manish/results/commit/0c33ca8fd05af7bed87f2fb41d4b044d7760c161', commit_message='end of training', commit_description='', oid='0c33ca8fd05af7bed87f2fb41d4b044d7760c161', pr_url=None, pr_revision=None, pr_num=None)

In [1]:
#testing and loading model

import torch, gc
gc.collect()
torch.cuda.empty_cache()

import numpy as np
import pandas as pd
import os
from tqdm import tqdm
import bitsandbytes as bnb
import torch
import torch.nn as nn
import transformers
from datasets import Dataset
from peft import LoraConfig, PeftConfig
from trl import SFTTrainer
from transformers import (AutoModelForCausalLM,
                          AutoTokenizer,
                          BitsAndBytesConfig,
                          TrainingArguments,
                          pipeline,
                          logging)
from sklearn.metrics import (accuracy_score,
                             classification_report,
                             confusion_matrix)
from sklearn.model_selection import train_test_split

from datasets import load_dataset

In [5]:
#teasting----1

# Ruta del modelo guardado en el dataset de Kaggle
from peft import LoraConfig, PeftModel

device_map = {"": 0}
PEFT_MODEL = "kr-manish/Llama-2-7b-chat-fine-tune-text-to-python"
#model_name = "NousResearch/Llama-2-7b-hf"

# Cargar la configuración del modelo
config = PeftConfig.from_pretrained(PEFT_MODEL)

# Cargar el modelo
model = AutoModelForCausalLM.from_pretrained(
    config.base_model_name_or_path,
    low_cpu_mem_usage=True,
    return_dict=True,
    #quantization_config=bnb_config,
    device_map="auto",
    #trust_remote_code=True,
    torch_dtype=torch.float16,
)

# Cargar el tokenizador
tokenizer=AutoTokenizer.from_pretrained(config.base_model_name_or_path)
tokenizer.pad_token = tokenizer.eos_token

# Cargar el modelo PEFT
load_model = PeftModel.from_pretrained(model, PEFT_MODEL)

input_text ="Program to convert Centimeters to Pixels | Function to convert centimeters to pixels ; Driver Code"
prompt_test = input_text
pipe_test = pipeline(task="text-generation",
                model=load_model,
                tokenizer=tokenizer,
                max_length =200,
                #max_new_tokens =25,
                )
#result_test = pipe_test(prompt_test)
#answer_test = result_test[0]['generated_text']
#answer_test
#or
result = pipe_test(f"<s>[INST] {input_text} [/INST]")
print(result[0]['generated_text'])

/usr/local/lib/python3.10/dist-packages/huggingface_hub/utils/_token.py:88: UserWarning: 
The secret `HF_TOKEN` does not exist in your Colab secrets.
To authenticate with the Hugging Face Hub, create a token in your settings tab (https://huggingface.co/settings/tokens), set it as secret in your Google Colab and restart your session.
You will be able to reuse this secret in all of your notebooks.
Please note that authentication is recommended but still optional to access public models or datasets.
  warnings.warn(


Loading checkpoint shards:   0%|          | 0/2 [00:00<?, ?it/s]

/usr/local/lib/python3.10/dist-packages/transformers/generation/configuration_utils.py:410: UserWarning: `do_sample` is set to `False`. However, `temperature` is set to `0.9` -- this flag is only used in sample-based generation modes. You should set `do_sample=True` or unset `temperature`. This was detected when initializing the generation config instance, which means the corresponding file may hold incorrect parameterization and should be fixed.
  warnings.warn(
/usr/local/lib/python3.10/dist-packages/transformers/generation/configuration_utils.py:415: UserWarning: `do_sample` is set to `False`. However, `top_p` is set to `0.6` -- this flag is only used in sample-based generation modes. You should set `do_sample=True` or unset `top_p`. This was detected when initializing the generation config instance, which means the corresponding file may hold incorrect parameterization and should be fixed.
  warnings.warn(
/usr/local/lib/python3.10/dist-packages/transformers/generation/configuratio

adapter_model.safetensors:   0%|          | 0.00/134M [00:00<?, ?B/s]

The model 'PeftModelForCausalLM' is not supported for text-generation. Supported models are ['BartForCausalLM', 'BertLMHeadModel', 'BertGenerationDecoder', 'BigBirdForCausalLM', 'BigBirdPegasusForCausalLM', 'BioGptForCausalLM', 'BlenderbotForCausalLM', 'BlenderbotSmallForCausalLM', 'BloomForCausalLM', 'CamembertForCausalLM', 'LlamaForCausalLM', 'CodeGenForCausalLM', 'CpmAntForCausalLM', 'CTRLLMHeadModel', 'Data2VecTextForCausalLM', 'ElectraForCausalLM', 'ErnieForCausalLM', 'FalconForCausalLM', 'FuyuForCausalLM', 'GemmaForCausalLM', 'GitForCausalLM', 'GPT2LMHeadModel', 'GPT2LMHeadModel', 'GPTBigCodeForCausalLM', 'GPTNeoForCausalLM', 'GPTNeoXForCausalLM', 'GPTNeoXJapaneseForCausalLM', 'GPTJForCausalLM', 'LlamaForCausalLM', 'MarianForCausalLM', 'MBartForCausalLM', 'MegaForCausalLM', 'MegatronBertForCausalLM', 'MistralForCausalLM', 'MixtralForCausalLM', 'MptForCausalLM', 'MusicgenForCausalLM', 'MvpForCausalLM', 'OpenLlamaForCausalLM', 'OpenAIGPTLMHeadModel', 'OPTForCausalLM', 'PegasusForCa

<s>[INST] Program to convert Centimeters to Pixels | Function to convert centimeters to pixels ; Driver Code [/INST] def convertCentimetersToPixels ( cm ) : NEW_LINE INDENT pixels = cm / 2.54 NEW_LINE return pixels NEW_LINE DEDENT cm = 10 NEW_LINE print ( convertCentimetersToPixels ( cm ) ) NEW_LINE cm = 20 NEW_LINE print ( convertCentimetersToPixels ( cm ) ) NEW_LINE cm = 30 NEW_LINE print ( convertCentimetersToPixels ( cm ) ) NEW_LINE cm = 40 NEW_LINE print ( convertCentimetersToPixels ( cm ) ) NEW_LINE cm = 50 NEW_LINE print ( convertCentimetersToPixels ( cm ) ) NEW_LINE cm = 60 NEW


In [23]:
dataset_val['text'][0]

'<s>[INST] Find maximum of minimum for every window size in a given array | An efficient Python3 program to find maximum of all minimums of windows of different sizes ; Used to find previous and next smaller ; Initialize elements of left [ ] and right [ ] ; Fill elements of left [ ] using logic discussed on www . geeksforgeeks . org / next - greater - element https : ; Empty the stack as stack is going to be used for right [ ] ; Fill elements of right [ ] using same logic ; Create and initialize answer array ; Fill answer array by comparing minimums of all . Lengths computed using left [ ] and right [ ] ; Length of the interval ; arr [ i ] is a possible answer for this Length \' Len \' interval , check if arr [ i ] is more than max for \'Len   ; Some entries in ans [ ] may not be filled yet . Fill them by taking values from right side of ans [ ] ; Print the result ; Driver Code [/INST] def printMaxOfMin ( arr , n ) : NEW_LINE INDENT s = [ ] NEW_LINE left = [ - 1 ] * ( n + 1 ) NEW_LINE 